In [1]:
import folium
from src.apikeys import MONGO
from src import process_tweets
from pymongo import MongoClient
import pandas as pd

In [2]:
tweet_processor = process_tweets.TweetProcessor('../models/tfidf_logistic_reg.pk')

In [3]:
client = MongoClient('mongodb://{}:{}@localhost:27017'.format(MONGO.USER, MONGO.PASSWORD))

In [4]:
database = client['twitter_database']

In [5]:
database.collection_names()

['test',
 'broncos_raiders',
 'available_trends',
 'test_method',
 'patriots_panthers']

In [6]:
table = database['patriots_panthers']

In [7]:
df = pd.DataFrame([tweet_processor.process_predict(tweet) for 
                   tweet in table.find({'user.location':{'$ne':None}}).limit(500)],
                 columns=['state','time','sentiment'])
df.head()

state                      time  sentiment
0        Virginia 2017-10-01 16:54:59+00:00   0.491284
1         Florida 2017-10-01 16:54:59+00:00   0.491284
2  North Carolina 2017-10-01 16:55:00+00:00   0.491284
3  North Carolina 2017-10-01 16:55:00+00:00   0.000587
4        New York 2017-10-01 16:55:01+00:00   0.491284

In [8]:
df_grouped = df[['state','sentiment']].groupby('state').mean()
df_grouped.head(10)

sentiment
state                 
Alabama       0.450441
Arizona       0.329039
Arkansas      0.339833
California    0.498255
Connecticut   0.330644
Delaware      0.491284
Florida       0.457619
Georgia       0.555977
Illinois      0.401608
Indiana       0.549040

In [10]:
from src.visualization import visualize_count
my_map = visualize_count(df)
my_map

In [11]:
import folium
import json
import pandas as pd 
import numpy as np
import geopandas as gpd

In [12]:
gdf = gpd.read_file('../data/state_geojson.json')
gdf.head()

name abbr  \
0                                American Samoa   AS   
1                                        Nevada   NV   
2                                       Arizona   AZ   
3                                     Wisconsin   WI   
4  Commonwealth of the Northern Mariana Islands   MP   

                                            geometry  
0                                                 ()  
1  POLYGON ((-114.04392 40.68928, -114.04558 40.4...  
2  POLYGON ((-114.63332 34.87057, -114.63349 35.0...  
3  POLYGON ((-87.815602 42.492729, -87.81626 42.4...  
4                                                 ()

In [13]:


merged = gdf.merge(df_grouped, left_on='name', right_index=True)
spatial_gdf = gpd.GeoDataFrame(merged.iloc[:, [0, 2]])
data_df = merged.iloc[:, [0, 3]]
data_df.head()

name  sentiment
1     Nevada   0.596592
2    Arizona   0.329039
3  Wisconsin   0.491284
5    Georgia   0.555977
7     Kansas   0.491284

In [16]:
df_grouped['name'] = df_grouped.index
df_grouped.head()

sentiment         name
state                              
Alabama       0.450441      Alabama
Arizona       0.329039      Arizona
Arkansas      0.188382     Arkansas
California    0.498255   California
Connecticut   0.330644  Connecticut

In [14]:
geo_str = spatial_gdf.to_json()
threshold_scale = np.linspace(0.0, 1.0, 
                              6, dtype=float).tolist()


map1 = folium.Map(location=[-15., -60], 
                  tiles="Cartodb Positron",
                  zoom_start=2)

map1.choropleth(geo_data=geo_str,
              data=data_df,
              columns=['name', 'sentiment'],
              fill_color='RdBu',
              key_on='feature.properties.name',
              threshold_scale=threshold_scale
              )

map1



In [51]:
merged.head()

name abbr                                           geometry  \
1     Nevada   NV  POLYGON ((-114.04392 40.68928, -114.04558 40.4...   
2    Arizona   AZ  POLYGON ((-114.63332 34.87057, -114.63349 35.0...   
3  Wisconsin   WI  POLYGON ((-87.815602 42.492729, -87.81626 42.4...   
5    Georgia   GA  POLYGON ((-81.12387 32.29667, -81.156540000000...   
7     Kansas   KS  POLYGON ((-96.28415 36.99927, -96.55381 36.998...   

   sentiment  
1   0.512488  
2   0.503409  
3   0.498730  
5   0.496027  
7   0.490742

In [17]:
from src.visualization import visualize_count

In [18]:
df = pd.DataFrame([tweet_processor.process_predict(tweet) for 
                   tweet in table.find({'user.location':{'$ne':None}}).limit(500)],
                 columns=['state','time','sentiment'])
df.head()

state                      time  sentiment
0        Virginia 2017-10-01 16:54:59+00:00   0.491284
1         Florida 2017-10-01 16:54:59+00:00   0.491284
2  North Carolina 2017-10-01 16:55:00+00:00   0.491284
3  North Carolina 2017-10-01 16:55:00+00:00   0.000587
4        New York 2017-10-01 16:55:01+00:00   0.491284

In [19]:
map = visualize_count(df)

In [20]:
map